# Grid Search

Calling all models, far and wide!  Now is the time to battle to the DEATH!!!!

Just kidding, this is just a 

In [ ]:
# notebooks use their location as their working directory, so
# if we are in a subfolder, move to the main folder.  
# This however can safely be run multiple times
#setwd(M:/lecospec/lecospec)
if(!dir.exists("Functions/")){
    setwd("../")
    if(!dir.exists("Functions")){
        setwd("M:/lecospec/lecospec/")
    }
}
source("Functions/lecospectR.R", echo = FALSE)
# some features of this notebook will use this in the future, maybe.  I hope so, at least.
library(IRdisplay)

## Load the Data file names

This loads the data file names.  These are assumed to be the same across training data, labels, test data and test labels

In [ ]:
BASE_PATH <- "Data/gs/"
X_TRAIN_PATH <- paste0(BASE_PATH, "x_train/")
Y_TRAIN_PATH <- paste0(BASE_PATH, "y_train/")

X_TEST_PATH <- paste0(BASE_PATH, "x_test/")
Y_TEST_PATH <- paste0(BASE_PATH, "y_test/")

In [ ]:
training_data <- list.files(X_TRAIN_PATH)
#training_labels <- sort(list.files("Data/gs/y_train/"))# sort alphabetically to keep the files in the same order

In [ ]:
print(training_data)

In [ ]:
load_data <- function(filepath){
    data <- list()
    train_data_path <- paste0(X_TRAIN_PATH, file)
    train_labels_path <- paste0(Y_TRAIN_PATH, file)
    test_labels_path <- paste0(Y_TEST_PATH, file)
    test_data_path <- paste0(X_TEST_PATH, file)

    # verify that all the paths are valid.  If not, return NULL
    if(
        file.exists(train_data_path) &&
        file.exists(train_labels_path) &&
        file.exists(test_data_path) &&
        file.exists(test_labels_path)
    ) {
        # files all exist, so return the result
        data$x_train <- subset(read.csv(train_data_path), select=-c(X))
        data$y_train <- read.csv(train_labels_path, header = TRUE)$x %>% as.factor()
        data$x_test <- read.csv(test_data_path)
        data$y_test <- read.csv(test_labels_path, header = TRUE)$x %>% as.factor()

        return(data)
    } else {
        # a file is missing, so return NULL
        return( NULL )
    }

}

In [ ]:
model <- ranger::ranger(
        num.trees = 1000,
        case.weights = weights_by_pft,
        classification = TRUE,
        x=df,
        y=gs_train_labels[[i]]
    )
    print(model)


    model_predictions <- predict(
        model, 
        test_df
    )$prediction %>% as.factor()
    
    test_samples <- gs_samples[[i]] %>% as.factor()
    if(!("Forb" %in% levels(test_samples))){

        levels(test_samples) <- c(levels(test_samples), "Forb")
    }

    confusion_matrix <- caret::confusionMatrix(
        model_predictions, 
        test_samples,
        mode = "everything"
    )


    
    model_metadata <- list(
        uuid = model_id,
        variables = colnames(df),
        type = "Random Forest (Ranger)",
        preprocessing = gs_preprocessing[[i]],
        saved = paste0("mle/models/gs/", model_id, ".rda"),
        results = paste0("mle/experiments/gs/", model_id, "/")
    )

    metadata_save_path <- paste0("mle/metadata/", model_id, ".json")
    json_metadata_str <- rjson::toJSON(model_metadata)
    write(json_metadata_str, file=metadata_save_path)
    
    save(model, file = paste0("mle/models/gs/", model_id, ".rda"))


In [ ]:
parse_name <- function(filepath){
    name_no_extension <- stringi::stri_replace_last_fixed(filepath, ".csv", "")
    name_parts <-strsplit(name_no_extension, "_") %>% as.vector()
    #print(name_parts)

    variables <- list(
        source = name_parts[[1]]
    )

    if(length(name_parts) > 1){
        variables$outliers <- names_parts[[2]]
    } else {
        variables$outliers <- NULL
    }

    if(length(name_parts) > 2){
        variables$preprocessing <- name_parts[[3]]
    } else {
        variables$preprocessing <- NULL
    }

    print(variables)
    return(variables)
}

In [ ]:
add_model_to_manifest <- function(model_id, variables, logpath="./gs_manifest.csv"){
    if(!file.exists(logpath)){
        header <- "source,outliers,preprocessing,model_id"
        write(header, file = logpath)
    }

    line <- paste(
        variables$source %>% as.character(),
        collapse = ","
    )
    line <- paste0(line, ",", model_id)

    write(line, file=logpath, append = TRUE)
}

In [ ]:
log_model_results <- function(model_id, confusion_matrix, distribition, custom, logpath = "./gs.log"){
    # append performance data to the logs for later comparison
    sink(file = logpath, append = TRUE)
    print("-------------------------------------------------------")
    print("---------------------- Model Data ---------------------")
    
    print(paste0("Model Type: Ranger (Random Forest)"))
    print(paste0("Data Index: ",custom))
    print(paste0("Model UUID: ", model_id))
    print("---------------------- Confusion Matrix ---------------------")
    print(confusion_matrix)
    print("---------------------- Class Distribution ---------------------")
    print(distribition)
    print("-------------------------------------------------------")
    sink(NULL)
}

In [ ]:
for(file in training_data){

    print(file)
    # load all the data
    data <- load_data(file)
    #print(colnames(data$x_train))

    if(!is.null(data)){
        
        model <- ranger::ranger(
            num.trees = 1000,
            case.weights = targets_to_weights(data$y_train),
            classification = TRUE,
            x=data$x_train,
            y=data$y_train
        )

        #add forb if it's in the training data to avoid mismatch
        if(("Forb" %in% levels(data$y_train)) && !("Forb"  %in% levels(data$y_test))){
            levels(data$y_test) <- c(levels(data$y_test), "Forb")
            }

        print(levels(data$y_test))

        # create predictions (ranger)
        model_predictions <- predict(
            model, 
            data$x_test
        )$prediction %>% as.factor()

        # generate the confusion matrix
        confusion_matrix <- caret::confusionMatrix(
            model_predictions, 
            data$y_test,
            mode = "everything"
        )

        # generate an id to uniquely identify the model
        model_id <- uuid::UUIDgenerate()

        # append performance data to the logs for later comparison
        log_model_results(
            model_id = model_id,
            confusion_matrix = confusion_matrix,
            custom = file,
            distribition = model_predictions %>% as.factor() %>% table())

        # track what levels are associated with the UUID
        add_model_to_manifest(
            model_id = model_id,
            variables = parse_name(file)
        )

        # save the model using the model UUID
        save(model, file = paste0("mle/models/gs/", model_id, ".rda"))
    }
}

In [ ]:
print((confusion_matrix$overall %>% as.list())$Accuracy)

In [ ]:
length(data$y_test)
nrow(data$x_test)

In [ ]:
length(data$y_train)
nrow(data$x_train)

In [ ]:
model_index <- read.csv("./gs_manifest.csv")

In [103]:
model_index

source outliers preprocessing model_id                            
1  grd    clipped  minmax        b5c8d838-c36c-4173-bb5b-7ddc91b685da
2  grd    clipped  raw           4750c1b3-54bd-44cf-be87-27694c109043
3  grd    clipped  robust        abc6db2a-23a5-40f8-bae7-2b82bccdc0dd
4  grd    clipped  standard      d68c5641-4197-4ec0-8103-34a256fe3203
5  grd    clipped  minmax        8a5a9be2-23f8-4752-ba42-a0592c4ecdae
6  grd    clipped  raw           cd46c134-bfc9-4938-a995-6e3fda63fba6
7  grd    clipped  robust        6251e8eb-2176-4ea6-bff0-5d91fb307ee3
8  grd    clipped  standard      41e7a280-412f-4aa7-a97b-15846d8b6b17
9  grd    imputed  minmax        b24c62a5-5bc9-4b32-98ee-7052773737e2
10 grd    imputed  raw           39f05ae1-9ca0-447e-880e-82c8756eb943
11 grd    imputed  robust        0e7979e9-fb87-4aa9-b265-5f1a6c4279e3
12 grd    imputed  standard      94c8396c-bae8-4bd0-b49e-56ba2ca56af1
13 grd    raw      minmax        47613d99-42c2-4145-8f31-c587adb3eb61
14 grd    raw      raw           e7e8f519-3784-443c-8c69-9039556b499a
15 grd    raw      robust        50bf7899-1f1c-458b-b10d-16736e44c8ff
16 grd    raw      standard      ad562f3f-029f-43da-8b64-0c1cfbc7a3b7
17 img    clipped  minmax        0831a1b8-80f1-43b0-98f6-878e5dbfbf57
18 img    clipped  raw           04905eb0-212f-4ac5-b910-13dd35d5f28b
19 img    clipped  robust        4860c51c-02ce-4530-aa65-517f1021e7af

TO DO: Add preprocessing selection to the next cell!

In [105]:
for(i in seq(nrow(model_index))){
    
    id <- model_index[i,"model_id"]
    print(id)
    model <- load_model(
        paste0("mle/models/gs/", id, ".rda")
    )

    save_path <- paste0("mle/experiments/gs/", id, "/")
    #print(names(model))
    print(model)
    if(!dir.exists(save_path)){
        dir.create(save_path)
    } 
    #print(quadrats[[3]])


   results <- validate_model(
       model, 
       save_path, 
       normalize_input = FALSE,
       standardize_input = FALSE,
       scale_input = FALSE,
       robust_scale_input = TRUE, 
       cluster = NULL)
   aggregated_results <- aggregate_results(save_path)

    plot_by_pft(
        aggregated_results,
        save_path = paste0(save_path, "aggregate.html"),
        open = FALSE
    )
#
    write_validation_table(
        aggregated_results,
        save_path = paste0(save_path, "table.html"),
        open = FALSE
    )


}

[1] "b5c8d838-c36c-4173-bb5b-7ddc91b685da"
Ranger result

Call:
 ranger::ranger(num.trees = 1000, case.weights = targets_to_weights(data$y_train),      classification = TRUE, x = data$x_train, y = data$y_train) 

Type:                             Classification 
Number of trees:                  1000 
Sample size:                      1343 
Number of independent variables:  214 
Mtry:                             14 
Target node size:                 1 
Variable importance mode:         none 
Splitrule:                        gini 
OOB prediction error:             18.56 % 
[1] "4750c1b3-54bd-44cf-be87-27694c109043"
Ranger result

Call:
 ranger::ranger(num.trees = 1000, case.weights = targets_to_weights(data$y_train),      classification = TRUE, x = data$x_train, y = data$y_train) 

Type:                             Classification 
Number of trees:                  1000 
Sample size:                      1343 
Number of independent variables:  214 
Mtry:                             14 


Using spline to predict value at new bands...

Beware the spectra are now partially smoothed.



    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
0.004657 0.040281 0.079833 0.077252 0.111162 0.166569 
    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
0.004364 0.039266 0.078478 0.076049 0.109991 0.169670 
    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
0.004364 0.039266 0.078478 0.076049 0.109991 0.169670 
    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
0.004364 0.039266 0.078478 0.076049 0.109991 0.169670 
[1] "Imputing..."


`.cols` has been renamed and is deprecated, please use `.vars`


       x              y            X397.593          X399.444      
 Min.   :-149   Min.   :63.81   Min.   :-1.0199   Min.   :-0.9250  
 1st Qu.:-149   1st Qu.:63.81   1st Qu.:-0.4323   1st Qu.:-0.4715  
 Median :-149   Median :63.81   Median : 0.0000   Median : 0.0000  
 Mean   :-149   Mean   :63.81   Mean   : 0.1151   Mean   : 0.0481  
 3rd Qu.:-149   3rd Qu.:63.81   3rd Qu.: 0.5677   3rd Qu.: 0.5285  
 Max.   :-149   Max.   :63.81   Max.   : 3.4763   Max.   : 2.1116  
    X401.296            X403.148             X405             X406.851       
 Min.   :-1.049083   Min.   :-1.18348   Min.   :-1.25635   Min.   :-1.26267  
 1st Qu.:-0.502961   1st Qu.:-0.60589   1st Qu.:-0.60723   1st Qu.:-0.59951  
 Median : 0.000000   Median : 0.00000   Median : 0.00000   Median : 0.00000  
 Mean   : 0.008998   Mean   :-0.08003   Mean   :-0.08523   Mean   :-0.07578  
 3rd Qu.: 0.497039   3rd Qu.: 0.39411   3rd Qu.: 0.39277   3rd Qu.: 0.40049  
 Max.   : 1.846751   Max.   : 1.67343   Max.   : 1.74903

...

Saving 6.67 x 6.67 in image



Simple feature collection with 1 feature and 3 fields
Geometry type: POLYGON
Dimension:     XY
Bounding box:  xmin: -145.9796 ymin: 65.40196 xmax: -145.9796 ymax: 65.40197
Geodetic CRS:  GCS_unknown
  CLASS_ID   CLASS_NAME AREA                       geometry
4        1 Twelvemile70  518 POLYGON ((-145.9796 65.4019...


Saving 6.67 x 6.67 in image



[1] "z"


Saving 6.67 x 6.67 in image

Saving 6.67 x 6.67 in image

Saving 6.67 x 6.67 in image

Saving 6.67 x 6.67 in image

